# Janus gym environment

In [10]:
import gym
from gym import spaces
import random
import stable_baselines3
from stable_baselines3.common.env_checker import check_env
from stable_baselines3 import DQN, DDPG
from math import sqrt
import numpy as np
import pandas as pd
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
from sklearn.model_selection import train_test_split
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
from sklearn import preprocessing
from sklearn.datasets import make_regression
import warnings
warnings.filterwarnings('ignore') 
import math
import pickle

class Janus(gym.Env):
    metadata = {'render.modes': ['human']}
    template_filename = 'data/dataset-S_public/public/dataset_S-{}.csv'

    def __init__(self, idx=47):
        super(Janus, self).__init__()
        #actions: move on the grid, by continuous value in -1,1
        #0,0 no move
        #based on 94 controlable parameters
        #"We recommend you to use a symmetric and normalized Box action space (range=[-1, 1]) ", we will multiply effect by 2
#         self.action_space = spaces.Box(low=-1.0, high=1.0, shape=(94, ))
        #we focus on the 1 most influencal action
        nbr_actions = 4
        self.action_space = spaces.Box(low=-1.0, high=1.0, shape=(nbr_actions, ))
    

        # all the observation_space
        self.observation_space = spaces.Box(low=-1.0, high=1.0, shape=(228, ))

        file1 = pd.read_csv(self.template_filename.format('file1'), index_col=0)
        file2 = pd.read_csv(self.template_filename.format('file2'), index_col=0)
        file3 = pd.read_csv(self.template_filename.format('file3'), index_col=0)
        vav = pd.read_csv(self.template_filename.format('VAV'), index_col=0)
        self.ti = pd.read_csv(self.template_filename.format('TI'), index_col=0)
        self.ts = pd.read_csv(self.template_filename.format('TS'), index_col=0)
        x_df = file1.copy()
        x_df = x_df.loc[:, (x_df != 0).any(axis=0)]  ## remove static columns
        x_df = x_df.fillna(x_df.mean())  ## replace nan with mean

        self.y_df = file2.copy()
        self.y_df.dropna(how='all', axis=1,
                    inplace=True)  ## drop full tempty columns
        self.y_df = self.y_df.fillna(self.y_df.mean())

        self.vav_df = vav.copy()
        # Dropping few columns
        for dataset in [self.y_df, self.vav_df, self.ti, self.ts]:
            dataset.drop(['target_1', 'target_2', 'target_3', 'target_4'],
                  axis=1,
                  inplace=True)  #to simplify with a 2-dimension target space

        print('features shape: {}, \ntargets shape: {}'.format(
            x_df.shape, self.y_df.shape))

        x_train, x_test, y_train, y_test = train_test_split(x_df,
                                                            self.y_df,
                                                            test_size=0.1,
                                                            random_state=14)
        print('\nLength of train is {}, test is {}'.format(
            len(x_train), len(x_test)))
        ## Random forest
        filename = 'data/models/janus_RF.pkl'  # janus_LinearReg, janus_RF

        # pickle.dump(ml_model, open(filename, 'wb'))

        # # load the model from disk
        self.ml_model = pickle.load(open(filename, 'rb'))
        print(f'R squared: {self.ml_model.score(x_test, y_test.values):0.04f}')

        self.full_x = file3.copy()[x_df.columns]
        self.full_x = self.full_x.fillna(x_df.mean())
        
        self.partial_x = x_train.copy()

        inferred_y = pd.DataFrame(self.ml_model.predict(self.full_x),
                                  columns=self.y_df.columns)

        # list of [min, max, step, range] for each var
        scale = 100
        decimals = 3
        
        self.list_important_actions = np.argsort(self.ml_model.feature_importances_[:94])[::-1][:nbr_actions]

        ## get limits for Rewards
        self.output_steps = [round((self.y_df[i].max() - self.y_df[i].min())/scale, decimals) \
                        for i in self.y_df.columns]
        print('Output steps: ', self.output_steps)
        
        self.idx=idx

    def reset(self):
#         self.current_position = self.revert_to_obs_space(
#             self.full_x.sample().values.reshape(-1), self.full_x)
#         random.seed(13)
#         idx = random.randint(0,len(janus_env.partial_x)-1)
        self.current_position = self.revert_to_obs_space(
            self.full_x.iloc[self.idx].values.reshape(-1), self.full_x)
        
        
        # to fix The observation returned by the `reset()` method does not match the given observation space
        # maybe won't happen on linux
        # on windows looks like float64 is the defautl for pandas -> numpy and gym expects float32 (contains tries to cast to dtype(float32))
        self.current_position = self.current_position.astype('float32')
        
        self.last_action = self.current_position[self.list_important_actions]
        self.last_effect = False
        self.global_reward = 0
        self.episode_length = 0
        #print(f'reset at position {self.current_position[:10]}...')
        return self.current_position

    def step(self, action):
#         self.current_position[0:len(action)] = action
        for index, act in enumerate(self.list_important_actions):
            self.current_position[act]=action[index]
        self.last_action = action
        self.episode_length += 1
        done = False
        
        reward = self.reward(
            self.convert_to_real_obs(self.current_position,
                                     self.full_x).values.reshape(1,-1))
        if (reward >= -0.1*self.y_df.shape[1]):
            done = True
        
#         print(f'target reached {done} reward {reward:0.03f} n° step {self.episode_length} action {self.last_action} done threeshold {-0.1*self.y_df.shape[1]:0.03f}')
        
        if done:
            reward += 100
        
        if self.episode_length>100:
            print('episode too long -> reset')
            done = True
            
#         if (max(abs(action))==1):
#             # if on border, we kill episode
#             print('border reached -> done -> reset')
#             reward -= 50
#             done = True
            

        self.global_reward += reward
#         print(f'  reward {reward:0.03f} global reward {self.global_reward:0.03f} done {done} action {action} step {self.episode_length}')
        return self.current_position, reward, done, {}

    def render(self):
        print(
            f'position {self.current_position[:10]}, action {self.last_action[:5]}, effect {self.last_effect}, done {done}, global_reward {self.global_reward:0.03f}'
        )

    def convert_to_real_obs(self, observation, observation_dataset):
        '''
        to convert an observation from observation space ([-1, 1],325) to  real world
        -1 matches with min() of each column
        1 matches with max() of each column
        
        observation: instance of observation_space
        observation_dataset: the full real dataset (obfuscated in that case)
        '''
        return (observation + np.ones(self.observation_space.shape)) / 2 * (
            observation_dataset.max() -
            observation_dataset.min()) + observation_dataset.min()

    def revert_to_obs_space(self, real_observation, observation_dataset):
        '''
        to revert an observation sample (from real world) to observation space
        min() of each column will match with -1
        max() of each column will match with +1
        
        real_observation: instance of real_world
        observation_dataset: the full real dataset (obfuscated in that case)
        '''
        return np.nan_to_num(
            2 * (real_observation - observation_dataset.min()) /
            (observation_dataset.max() - observation_dataset.min()) -
            np.ones(self.observation_space.shape)).reshape(-1)

    def reward(self, observation):
        ''' Discrete reward 
        observation if from real world not observation space
        '''

        new_y = self.ml_model.predict(observation).reshape(-1)
#         return self.continuous_reward_clown_hat(new_y)
        return self.reward_archery(new_y)

    def discrete_reward(self, new_y):
        ''' Discrete reward '''

        new_val = [
            sqrt((self.vav_df.iloc[:, i].values[0] - new_y[i])**2)
            for i in range(len(new_y))
        ]
        k = 10
        k1 = 1
        if new_val[0] < k * self.output_steps[0] and new_val[
                1] < k * self.output_steps[1]:
            reward = 1  #dans les 10% d'amplitude max autour de la vav
            if new_val[0] < k1 * self.output_steps[0] and new_val[
                    1] < k1 * self.output_steps[1]:
                reward = 10  #dans les 1% d'amplitude max autour de la vav
                on_target = True
#                 print('On Target : ', new_y)
        else:
            reward = -1
        return reward
    
    
    
    def continuous_reward_clown_hat(self, new_y):
        ''' Continuous reward '''
        final_reward = 0 

        for i in range(len(new_y)):
            reward = -9
            if ( self.ti.iloc[:,i].values[0] <=  new_y[i] <= self.ts.iloc[:,i].values[0]):
                if ( new_y[i] >= self.vav_df.iloc[:,i].values[0] ):
                    reward = 1-(new_y[i]-self.vav_df.iloc[:,i].values[0])/(self.ts.iloc[:,i].values[0]-self.vav_df.iloc[:,i].values[0])
                else:
                    reward = 1-(self.vav_df.iloc[:,i].values[0]-new_y[i])/(self.vav_df.iloc[:,i].values[0]-self.ti.iloc[:,i].values[0])
            reward += -1
            final_reward+=reward
    #         print(f'reward {reward} final_reward {final_reward} i {i}')

        if (final_reward>0.7*len(new_y)):
            on_target = True
    #         print('On Target : ', new_y)

        return final_reward

    def reward_archery(self, new_y):
        ''' Continuous reward '''
        final_reward = 0 
        
        ti_target_0 = self.ti.iloc[:,0].values[0]
        ts_target_0 = self.ts.iloc[:,0].values[0]
        ti_target_5 = self.ti.iloc[:,1].values[0]
        ts_target_5 = self.ts.iloc[:,1].values[0]
        x, y = new_y[0], new_y[1]
        if ( (ti_target_0*0.10 <= x <= ts_target_0*0.10) & ( ti_target_5*0.10 <= y <= ts_target_5*0.10 )):
            reward = 0
        else:
            if ( (ti_target_0*0.50 <= x <= ts_target_0*0.50) & ( ti_target_5*0.50 <= y <= ts_target_5*0.50 )):
                reward = -2
            else:
                if ( (ti_target_0 <= x <= ts_target_0) & ( ti_target_5 <= y <= ts_target_5 )):
                    reward = -5
                else:
                    reward = -20
        final_reward = reward
        return final_reward


In [6]:
janus_env = Janus()
from stable_baselines3.common.env_checker import check_env

check_env(janus_env)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


# SAC training

In [127]:
from stable_baselines3 import SAC

janus_env = Janus()
check_env(janus_env)

model_janus_sac = SAC("MlpPolicy", janus_env, verbose=2,tensorboard_log="./tensorboard/")
model_janus_sac.learn(total_timesteps=100000, log_interval=4, tb_log_name="janus partial sac")

janus_env.reset()
for i in range(100):
    action, _ = model_janus_sac.predict(janus_env.current_position)
    print(f'action {action}')
    obs, rewards, done, info = janus_env.step(action)
    janus_env.render()
    if done: break
janus_env.close()

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6550
Output steps:  [0.064, 0.057]
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/janus partial sac_3
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 27       |
|    time_elapsed    | 14       |
|    total timesteps | 404      |
| train/             |          |
|    actor_loss      | 0.392    |
|    critic_loss     | 0.0128   |
|    ent_coef        | 0.913    |
|    ent_coef_loss   | -0.153   |
|    learning_rate   | 0.0003   |
|    n_updates       | 303      |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/   

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 60       |
|    fps             | 24       |
|    time_elapsed    | 244      |
|    total timesteps | 6060     |
| train/             |          |
|    actor_loss      | 16.6     |
|    critic_loss     | 0.957    |
|    ent_coef        | 0.168    |
|    ent_coef_loss   | -3.01    |
|    learning_rate   | 0.0003   |
|    n_updates       | 5959     |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 64       |
|    fps             | 24       |
|    time_elapsed    | 260      |
|    total timesteps | 6464     |
| train/             |          |
|    actor_loss      | 17.7     |
|    critic_loss     | 3.35     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 120      |
|    fps             | 23       |
|    time_elapsed    | 517      |
|    total timesteps | 12120    |
| train/             |          |
|    actor_loss      | 30.4     |
|    critic_loss     | 17.2     |
|    ent_coef        | 0.0301   |
|    ent_coef_loss   | -2.55    |
|    learning_rate   | 0.0003   |
|    n_updates       | 12019    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 124      |
|    fps             | 23       |
|    time_elapsed    | 536      |
|    total timesteps | 12524    |
| train/             |          |
|    actor_loss      | 31       |
|    critic_loss     | 3.8      |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 180      |
|    fps             | 22       |
|    time_elapsed    | 799      |
|    total timesteps | 18180    |
| train/             |          |
|    actor_loss      | 39.1     |
|    critic_loss     | 46.2     |
|    ent_coef        | 0.00898  |
|    ent_coef_loss   | -0.818   |
|    learning_rate   | 0.0003   |
|    n_updates       | 18079    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 184      |
|    fps             | 22       |
|    time_elapsed    | 817      |
|    total timesteps | 18584    |
| train/             |          |
|    actor_loss      | 39.4     |
|    critic_loss     | 17.5     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 240      |
|    fps             | 22       |
|    time_elapsed    | 1059     |
|    total timesteps | 24240    |
| train/             |          |
|    actor_loss      | 42.9     |
|    critic_loss     | 29       |
|    ent_coef        | 0.00689  |
|    ent_coef_loss   | 1.22     |
|    learning_rate   | 0.0003   |
|    n_updates       | 24139    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 244      |
|    fps             | 22       |
|    time_elapsed    | 1076     |
|    total timesteps | 24644    |
| train/             |          |
|    actor_loss      | 43.8     |
|    critic_loss     | 28.9     |
|    ent_coef 

...

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 840      |
|    fps             | 23       |
|    time_elapsed    | 3652     |
|    total timesteps | 84840    |
| train/             |          |
|    actor_loss      | 50.2     |
|    critic_loss     | 38.5     |
|    ent_coef        | 0.00897  |
|    ent_coef_loss   | 1.4      |
|    learning_rate   | 0.0003   |
|    n_updates       | 84739    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 844      |
|    fps             | 23       |
|    time_elapsed    | 3670     |
|    total timesteps | 85244    |
| train/             |          |
|    actor_loss      | 50.6     |
|    critic_loss     | 19.4     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 900      |
|    fps             | 23       |
|    time_elapsed    | 3923     |
|    total timesteps | 90900    |
| train/             |          |
|    actor_loss      | 50       |
|    critic_loss     | 19.9     |
|    ent_coef        | 0.00513  |
|    ent_coef_loss   | -1.88    |
|    learning_rate   | 0.0003   |
|    n_updates       | 90799    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 904      |
|    fps             | 23       |
|    time_elapsed    | 3941     |
|    total timesteps | 91304    |
| train/             |          |
|    actor_loss      | 50.1     |
|    critic_loss     | 9.91     |
|    ent_coef 

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 960      |
|    fps             | 23       |
|    time_elapsed    | 4196     |
|    total timesteps | 96960    |
| train/             |          |
|    actor_loss      | 51       |
|    critic_loss     | 29.2     |
|    ent_coef        | 0.00438  |
|    ent_coef_loss   | -0.846   |
|    learning_rate   | 0.0003   |
|    n_updates       | 96859    |
---------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -101     |
| time/              |          |
|    episodes        | 964      |
|    fps             | 23       |
|    time_elapsed    | 4214     |
|    total timesteps | 97364    |
| train/             |          |
|    actor_loss      | 50       |
|    critic_loss     | 10.2     |
|    ent_coef 

position [ 0.874066   -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.874066], effect False, done False, global_reward -24
action [0.96536136]
position [ 0.96536136 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.96536136], effect False, done False, global_reward -25
action [0.9551518]
position [ 0.9551518  -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.9551518], effect False, done False, global_reward -26
action [0.98472524]
position [ 0.98472524 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.98472524], effect False, done False, global_reward -27
action [0.29568815]
position [ 0.29568815 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ],

position [ 0.9500246  -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.9500246], effect False, done False, global_reward -62
action [0.8876209]
position [ 0.88762093 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.8876209], effect False, done False, global_reward -63
action [0.9898963]
position [ 0.9898963  -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.9898963], effect False, done False, global_reward -64
action [0.9649997]
position [ 0.96499968 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], action [0.9649997], effect False, done False, global_reward -65
action [0.99591553]
position [ 0.99591553 -0.76       -0.67567568 -0.52941176  0.93877551 -0.98089959
 -0.63076923 -0.63076923 -0.2         0.        ], ac

# TD3 training

In [63]:
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise

model_name = "janus partial td3 - reward clown hat noborder"

janus_env = Janus()
check_env(janus_env)

n_actions = janus_env.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))
action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

model_janus_td3 = TD3("MlpPolicy", janus_env, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.learn(total_timesteps=1000, log_interval=4, tb_log_name=model_name)
model_janus_td3.save("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarn

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/janus partial td3 - reward clown hat noborder_3


C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names



---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | 99.9     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 11       |
|    time_elapsed    | 0        |
|    total timesteps | 4        |
---------------------------------


...

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names



---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | 100      |
| time/              |          |
|    episodes        | 996      |
|    fps             | 9        |
|    time_elapsed    | 102      |
|    total timesteps | 996      |
| train/             |          |
|    actor_loss      | -100     |
|    critic_loss     | 0.00207  |
|    learning_rate   | 0.001    |
|    n_updates       | 895      |
---------------------------------


C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names

C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarn

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1        |
|    ep_rew_mean     | 100      |
| time/              |          |
|    episodes        | 1000     |
|    fps             | 9        |
|    time_elapsed    | 102      |
|    total timesteps | 1000     |
| train/             |          |
|    actor_loss      | -100     |
|    critic_loss     | 0.00292  |
|    learning_rate   | 0.001    |
|    n_updates       | 899      |
---------------------------------


C:\Users\F279814\AppData\Local\Continuum\anaconda3\envs\stablebaselines3\lib\site-packages\sklearn\base.py:442: UserWarning:

X does not have valid feature names, but RandomForestRegressor was fitted with feature names



In [101]:
def use_trained_RL_model():
    print(f'model used: {model_name}')

    model_janus_td3 = TD3("MlpPolicy", janus_env, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
    model_janus_td3.load("./data/"+model_name)

    janus_env.reset()
    for i in range(100):
        action, _ = model_janus_td3.predict(janus_env.current_position)
        print(f'action {action}')
        obs, rewards, done, info = janus_env.step(action)
        janus_env.render()
        if done: 
            print(f'done within {i+1} iterations')
            break
    janus_env.close()

In [104]:
def use_trained_RL_model_2(idx):
    janus_env = Janus(idx)
    check_env(janus_env)

    # model_name = "janus partial td3 - reward clown hat"
    print(f'model used: {model_name}')
    model_janus_td3 = TD3("MlpPolicy", janus_env, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
    model_janus_td3.load("./data/"+model_name)

    janus_env.reset()
    new_y = janus_env.ml_model.predict(janus_env.convert_to_real_obs(janus_env.current_position,
                                         janus_env.full_x).values.reshape(1,-1)).reshape(-1)
    print(f'init results:  {new_y} reward {janus_env.continuous_reward_clown_hat(new_y):0.03f} action {janus_env.last_action}')

    for i in range(100):
        action, _ = model_janus_td3.predict(janus_env.current_position)
    #     print(f'action {action}')
        obs, rewards, done, info = janus_env.step(action)
    #     janus_env.render()
        if done: 
            print(f'done within {i+1} iterations')
            break
    new_y = janus_env.ml_model.predict(janus_env.convert_to_real_obs(janus_env.current_position,
                                         janus_env.full_x).values.reshape(1,-1)).reshape(-1)
    print(f'new results after {i+1} iterations:  {new_y} associated reward {janus_env.continuous_reward_clown_hat(new_y):0.03f}  action {janus_env.last_action}')
    return janus_env.vav_df

In [105]:
use_trained_RL_model_2(2230)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
model used: EXP6 - IDX 2230 - reward cont clown
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
init results:  [-1.16214975  1.33550241] reward -10.419 action [ 0.26435483  0.9591837   0.32765958 -0.9531479 ]
new results after 100 iterations:  [-1.07584052  1.08965022] associated reward -1.322  action [ 0.10438347 -0.01168418 -0.00563693 -0.00568449]


target_0  target_5
0  0.984997 -0.170155

# plot reward functions

In [66]:
janus_env = Janus()
# print(janus_env.vav_df)
# print(janus_env.ti)
# print(janus_env.ts)

inf_x = janus_env.ti.iloc[0][0]
sup_x = janus_env.ts.iloc[0][0]
inf_y = janus_env.ti.iloc[0][1]
sup_y = janus_env.ts.iloc[0][1]
inf_limx = min(inf_x, janus_env.y_df.min()[0])
sup_limx = max(sup_x, janus_env.y_df.max()[0])
inf_limy = min(inf_y, janus_env.y_df.min()[1])
sup_limy = max(sup_y, janus_env.y_df.max()[1])


features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


## create dataframe with reward values

In [8]:
def keep_reward_content(reward=janus_env.continuous_reward_clown_hat, reward_name = 'janus_env.continuous_reward_clown_hat'):

    X = np.arange(inf_limx-3, sup_limx+3, 0.2)
    Y = np.arange(inf_limy-3, sup_limy+3, 0.2)
    xyz_content=[]
    for x in X:
        for y in Y:
            xyz_content.append([x, y, reward([x,y])])
    xyz_content = pd.DataFrame(xyz_content, columns=['x', 'y', 'z'])
    xyz_content.to_csv('./data/'+reward_name+'.csv')
        

In [22]:
keep_reward_content(janus_env.continuous_reward_clown_hat, 'continuous_reward_clown_hat')

## plot reward function

In [12]:
import plotly.express as px

xyz_content = pd.read_csv('./data/continuous_reward_clown_hat.csv', index_col=0)
fig = px.scatter_3d(xyz_content, x='x', y='y', z='z',
              color='z')
fig.show()

# visualiser les progrès par RL: qualité avant et après

In [78]:
janus_env = Janus()
janus_env.reset()
inf_x = janus_env.ti.iloc[0][0]
sup_x = janus_env.ts.iloc[0][0]
inf_y = janus_env.ti.iloc[0][1]
sup_y = janus_env.ts.iloc[0][1]
inf_limx = min(inf_x, janus_env.y_df.min()[0])
sup_limx = max(sup_x, janus_env.y_df.max()[0])
inf_limy = min(inf_y, janus_env.y_df.min()[1])
sup_limy = max(sup_y, janus_env.y_df.max()[1])
vav_x = janus_env.vav_df.iloc[0].values[0]
vav_y = janus_env.vav_df.iloc[0].values[1]

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


In [111]:
def positionne_point_idx(janus_env, fig):
    print(f'Index de l observation {janus_env.idx}')
    current_position = janus_env.revert_to_obs_space(janus_env.full_x.iloc[janus_env.idx].values.reshape(-1), janus_env.full_x)
    current_position = current_position.astype('float32')
    current_y = janus_env.ml_model.predict(janus_env.convert_to_real_obs(current_position,
                                     janus_env.full_x).values.reshape(1,-1)).reshape(-1)
    print(f'init results:  {current_y} reward {janus_env.continuous_reward_clown_hat(current_y):0.03f} action {janus_env.last_action}')
    fig.add_trace(go.Scatter(x=[current_y[0]], y=[current_y[1]], name='point initial obs '+str(janus_env.idx)))

    
    for i in range(100):
        action, _ = model_janus_td3.predict(janus_env.current_position)
    #     print(f'action {action}')
        obs, rewards, done, info = janus_env.step(action)
    #     janus_env.render()
        if done: 
            print(f'done within {i+1} iterations')
            break
    new_y = janus_env.ml_model.predict(janus_env.convert_to_real_obs(janus_env.current_position,
                                         janus_env.full_x).values.reshape(1,-1)).reshape(-1)
    
    print(f'final results:  {new_y} reward {janus_env.continuous_reward_clown_hat(new_y):0.03f} action {janus_env.last_action}')
    fig.add_trace(go.Scatter(x=[new_y[0]], y=[new_y[1]], name='point final obs '+str(janus_env.idx)))
    
    

In [112]:
import plotly.graph_objects as go


def visualise_avant_apres(janus_env):
    fig = go.Figure()

    fig.update_xaxes(title_text='target_0', range=[inf_limx-3, sup_limx+3])
    fig.update_yaxes(title_text='target_5', range=[inf_limy-3, sup_limy+3])

    fig.add_trace(go.Scatter(x=[inf_x,inf_x,sup_x,sup_x, inf_x, None, vav_x], y=[inf_y,sup_y,sup_y, inf_y, inf_y, None, vav_y], fill="toself", name='TI, TS, VAV'))
    positionne_point_idx(janus_env, fig)
    fig.update_layout({'showlegend': True, 'title':'Position de la qualité, avant, après'})
    fig.show()

# visualiser les reward de toutes les tombées

## toutes les tombées (13639)

In [93]:
#13000 tombees
janus_env.full_x
#782 tombees MGQA
janus_env.y_df

full_prediction = janus_env.ml_model.predict(janus_env.full_x)
full_prediction
reward_df = pd.DataFrame(full_prediction, columns=['target_0', 'target_5'])
reward_df

reward_df['reward']=reward_df.apply(lambda x: janus_env.continuous_reward_clown_hat([x[0], x[1]]), axis=1)

In [94]:
reward_df

target_0  target_5    reward
0      1.272392 -0.128161 -0.147244
1      1.318423 -0.261984 -0.182810
2      1.220757 -0.376870 -0.168672
3      1.107798 -0.441253 -0.133282
4      1.180480 -0.390166 -0.153368
...         ...       ...       ...
13634  1.019059  0.156182 -0.106775
13635  0.851899  0.098368 -0.137423
13636  0.799811  0.108181 -0.164722
13637  0.880290  0.112144 -0.127860
13638  1.005741  0.126503 -0.092244

[13639 rows x 3 columns]

In [95]:
import pandas as pd
pd.options.plotting.backend = "plotly"

fig = reward_df.plot()
fig.show()

# EXP 6 - IDX 2230

In [97]:
janus_env_2230 = Janus(2230)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


In [100]:
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
import warnings
warnings.filterwarnings('ignore') 

model_name = "EXP6 - IDX 2230 - reward cont clown"

janus_env_2230 = Janus(2230)
check_env(janus_env_2230)

n_actions = janus_env_2230.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))
action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

model_janus_td3 = TD3("MlpPolicy", janus_env_2230, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.learn(total_timesteps=10000, log_interval=4, tb_log_name=model_name)
model_janus_td3.save("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/EXP6 - IDX 2230 - reward cont clown_3
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -142     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 17       |
|    time_elapsed    | 23       |
|    total timesteps | 404      |
| train/             |          |
|    actor_loss      | 2.15     |
|    critic_loss     | 2.65     |
|    learning_rate   | 0.001    |
|    n_updates       | 303      |
---------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too lo

episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -131     |
| time/              |          |
|    episodes        | 56       |
|    fps             | 15       |
|    time_elapsed    | 372      |
|    total timesteps | 5656     |
| train/             |          |
|    actor_loss      | 15.6     |
|    critic_loss     | 4.59     |
|    learning_rate   | 0.001    |
|    n_updates       | 5555     |
---------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -131     |
| time/              |          |
|    episodes        | 60       |
|    fps             | 15       |
|    time_elapsed    | 399      |
|    total

In [114]:
janus_env_2230 = Janus(2230)
janus_env_2230.reset()
print(f'model used: {model_name}')
model_janus_td3 = TD3("MlpPolicy", janus_env, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.load("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
model used: EXP6 - IDX 2230 - reward cont clown
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [115]:
visualise_avant_apres(janus_env_2230)

Index de l observation 2230
init results:  [-1.16214975  1.33550241] reward -10.419 action [ 0.26435483  0.9591837   0.32765958 -0.9531479 ]
final results:  [-1.02890042  1.03092976] reward -1.284 action [-0.13309348 -0.09316564 -0.06613958  0.12552571]


# EXP 7 - IDX 11926

In [116]:
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
import warnings
warnings.filterwarnings('ignore') 

model_name = "EXP7 - IDX 11926 - reward cont clown"

idx = 11926

janus = Janus(idx)
check_env(janus)

n_actions = janus.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))
action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

model_janus_td3 = TD3("MlpPolicy", janus, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.learn(total_timesteps=10000, log_interval=4, tb_log_name=model_name)
model_janus_td3.save("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/EXP7 - IDX 11926 - reward cont clown_1
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -1.06e+03 |
| time/              |           |
|    episodes        | 4         |
|    fps             | 16        |
|    time_elapsed    | 24        |
|    total timesteps | 404       |
| train/             |           |
|    actor_loss      | 14.3      |
|    critic_loss     | 0.341     |
|    learning_rate   | 0.001     |
|    n_updates       | 303       |
----------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> rese

episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -1.06e+03 |
| time/              |           |
|    episodes        | 64        |
|    fps             | 15        |
|    time_elapsed    | 429       |
|    total timesteps | 6464      |
| train/             |           |
|    actor_loss      | 141       |
|    critic_loss     | 336       |
|    learning_rate   | 0.001     |
|    n_updates       | 6363      |
----------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -1.06e+03 |
| time/              |           |
|    episodes        | 68        |
|    fps             | 15        |
|    time_elapsed    |

In [117]:
visualise_avant_apres(janus)

Index de l observation 11926
init results:  [-2.28332155 -2.36309252] reward -10.610 action [ 0.24048309  0.7755102  -0.23404256 -0.9677892 ]
final results:  [-1.63774366 -1.85793771] reward -10.469 action [ 1. -1.  1. -1.]


# move to reward archery and plot

On change de 

```python
    def reward(self, observation):
        ''' Discrete reward 
        observation if from real world not observation space
        '''
        new_y = self.ml_model.predict(observation).reshape(-1)
        return self.continuous_reward_clown_hat(new_y)
```

à
```python
    def reward(self, observation):
        ''' Discrete reward 
        observation if from real world not observation space
        '''
        new_y = self.ml_model.predict(observation).reshape(-1)
        return self.reward_archery(new_y)
```



In [11]:
janus_env = Janus()
# print(janus_env.vav_df)
# print(janus_env.ti)
# print(janus_env.ts)

inf_x = janus_env.ti.iloc[0][0]
sup_x = janus_env.ts.iloc[0][0]
inf_y = janus_env.ti.iloc[0][1]
sup_y = janus_env.ts.iloc[0][1]
inf_limx = min(inf_x, janus_env.y_df.min()[0])
sup_limx = max(sup_x, janus_env.y_df.max()[0])
inf_limy = min(inf_y, janus_env.y_df.min()[1])
sup_limy = max(sup_y, janus_env.y_df.max()[1])

keep_reward_content(janus_env.reward_archery, 'reward_archery')

import plotly.express as px

xyz_content = pd.read_csv('./data/reward_archery.csv', index_col=0)
fig = px.scatter_3d(xyz_content, x='x', y='y', z='z',
              color='z')
fig.show()

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]


# EXP 8 - archery - IDX  11926

In [13]:
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
import warnings
warnings.filterwarnings('ignore') 

model_name = "EXP8 - IDX 11926 - archery"

idx = 11926

janus = Janus(idx)
check_env(janus)

n_actions = janus.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))
action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

model_janus_td3 = TD3("MlpPolicy", janus, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.learn(total_timesteps=10000, log_interval=4, tb_log_name=model_name)
model_janus_td3.save("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/EXP8 - IDX 11926 - archery_1
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -2.02e+03 |
| time/              |           |
|    episodes        | 4         |
|    fps             | 16        |
|    time_elapsed    | 24        |
|    total timesteps | 404       |
| train/             |           |
|    actor_loss      | 26        |
|    critic_loss     | 0.647     |
|    learning_rate   | 0.001     |
|    n_updates       | 303       |
----------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode 

episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -2.02e+03 |
| time/              |           |
|    episodes        | 56        |
|    fps             | 16        |
|    time_elapsed    | 353       |
|    total timesteps | 5656      |
| train/             |           |
|    actor_loss      | 238       |
|    critic_loss     | 998       |
|    learning_rate   | 0.001     |
|    n_updates       | 5555      |
----------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
----------------------------------
| rollout/           |           |
|    ep_len_mean     | 101       |
|    ep_rew_mean     | -2.02e+03 |
| time/              |           |
|    episodes        | 60        |
|    fps             | 15        |
|    time_elapsed    |

visu reward archery toutes les tombées

In [14]:
full_prediction = janus.ml_model.predict(janus.full_x)
full_prediction
reward_df = pd.DataFrame(full_prediction, columns=['target_0', 'target_5'])
reward_df

reward_df['reward_archery']=reward_df.apply(lambda x: janus.reward_archery([x[0], x[1]]), axis=1)

In [16]:
reward_df.head()

target_0  target_5  reward_archery
0  1.272392 -0.128161              -2
1  1.318423 -0.261984              -2
2  1.220757 -0.376870              -2
3  1.107798 -0.441253              -2
4  1.180480 -0.390166              -2

In [17]:
import pandas as pd
pd.options.plotting.backend = "plotly"

fig = reward_df.plot()
fig.show()

# Fix notebook duplicated cells

In [29]:
import nbformat as nbf
from glob import glob

import uuid
def get_cell_id(id_length=8):
    return uuid.uuid4().hex[:id_length]

# your notebook name/keyword
nb_name = '03 - partial environnement for dataset S.ipynb'
notebooks = list(filter(lambda x: nb_name in x, glob("./*.ipynb", recursive=True)))

# iterate over notebooks
for ipath in sorted(notebooks):
    # load notebook
    ntbk = nbf.read(ipath, nbf.NO_CONVERT)
    
    cell_ids = []
    for cell in ntbk.cells:
        cell_ids.append(cell['id'])

    # reset cell ids if there are duplicates
    if not len(cell_ids) == len(set(cell_ids)): 
        for cell in ntbk.cells:
            cell['id'] = get_cell_id()

    nbf.write(ntbk, ipath)

# EXP 9 - archery - IDX 1926

In [30]:
from stable_baselines3 import TD3
from stable_baselines3.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise
import warnings
warnings.filterwarnings('ignore') 

model_name = "EXP9 - IDX 1926 - archery"

idx = 1926

janus = Janus(idx)
check_env(janus)

n_actions = janus.action_space.shape[-1]
action_noise = NormalActionNoise(mean=np.zeros(n_actions), sigma=0.1 * np.ones(n_actions))
action_noise = OrnsteinUhlenbeckActionNoise(mean=np.zeros(n_actions), sigma=float(0.5) * np.ones(n_actions))

model_janus_td3 = TD3("MlpPolicy", janus, action_noise=action_noise, verbose=2,tensorboard_log="./tensorboard/")
model_janus_td3.learn(total_timesteps=10000, log_interval=4, tb_log_name=model_name)
model_janus_td3.save("./data/"+model_name)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard/EXP9 - IDX 1926 - archery_2
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -306     |
| time/              |          |
|    episodes        | 4        |
|    fps             | 17       |
|    time_elapsed    | 22       |
|    total timesteps | 404      |
| train/             |          |
|    actor_loss      | 4.51     |
|    critic_loss     | 2.9      |
|    learning_rate   | 0.001    |
|    n_updates       | 303      |
---------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> rese

episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -231     |
| time/              |          |
|    episodes        | 56       |
|    fps             | 15       |
|    time_elapsed    | 371      |
|    total timesteps | 5656     |
| train/             |          |
|    actor_loss      | 24.3     |
|    critic_loss     | 11.8     |
|    learning_rate   | 0.001    |
|    n_updates       | 5555     |
---------------------------------
episode too long -> reset
episode too long -> reset
episode too long -> reset
episode too long -> reset
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 101      |
|    ep_rew_mean     | -229     |
| time/              |          |
|    episodes        | 60       |
|    fps             | 15       |
|    time_elapsed    | 399      |
|    total

In [32]:
idx = 1926

janus = Janus(idx)
janus.reset()
visualise_avant_apres(janus)

features shape: (782, 228), 
targets shape: (782, 2)

Length of train is 703, test is 79
R squared: 0.6441
Output steps:  [0.064, 0.057]
Index de l observation 1926
init results:  [0.95925564 1.83851258] reward -0.570 action [ 0.25700969  0.93877554  0.14893617 -0.95607615]
final results:  [0.68078712 1.49007435] reward -0.605 action [-1. -1.  1.  1.]
